In [1]:
import pandas as pd
import numpy as np
import os

DATA_DIR = os.path.join("..", "data") 

In [2]:
detailed_tourney_games_df = pd.concat([
    pd.read_csv(os.path.join(DATA_DIR, "MNCAATourneyDetailedResults.csv")).assign(League="M"),
    pd.read_csv(os.path.join(DATA_DIR, "WNCAATourneyDetailedResults.csv")).assign(League="W"),
])

detailed_tourney_games_df.sample(5, random_state=1)

Season  DayNum  WTeamID  WScore  LTeamID  LScore WLoc  NumOT  WFGM  \
808     2015     137     1320      71     1461      54    N      0    23   
682     2021     146     3257      60     3332      42    N      0    26   
1114    2019     154     1438      85     1403      77    N      1    27   
718     2022     138     3261      83     3238      77    H      0    30   
1217    2022     138     1116      53     1308      48    N      0    14   

      WFGA  ...  LFTM  LFTA  LOR  LDR  LAst  LTO  LStl  LBlk  LPF  League  
808     50  ...     3     9    4   18    14   12     2     3   17       M  
682     63  ...     4     5   14   23     7   14     5     6   10       W  
1114    59  ...    13    15    9   23     9    8     6     3   18       M  
718     74  ...    19    29   12   28    11   15     5     4   23       W  
1217    51  ...     6    10    4   32     8   17     4     4   15       M  

[5 rows x 35 columns]

In [3]:
detailed_reg_games_df = pd.concat([
    pd.read_csv(os.path.join(DATA_DIR, "MRegularSeasonDetailedResults.csv")).assign(League="M"), 
    pd.read_csv(os.path.join(DATA_DIR, "WRegularSeasonDetailedResults.csv")).assign(League="W"),
])

detailed_reg_games_df.sample(5, random_state=1)

Season  DayNum  WTeamID  WScore  LTeamID  LScore WLoc  NumOT  WFGM  \
27948     2008     110     1193      60     1180      51    A      0    22   
88315     2020      19     1345      81     1240      49    H      0    31   
1536      2003      59     1272      72     1116      67    A      0    23   
104465    2023      66     1186      92     1340      80    H      0    30   
85458     2019      86     1292      71     1412      65    H      0    25   

        WFGA  ...  LFTM  LFTA  LOR  LDR  LAst  LTO  LStl  LBlk  LPF  League  
27948     52  ...     7    12   14   20    13   10     4     3   16       M  
88315     56  ...    12    21   13   21    10    8     4     0   19       M  
1536      50  ...    14    20    5   17     8   13    10     2   25       M  
104465    51  ...    10    13   12   17    15   11    11     2   20       M  
85458     57  ...    15    22    5   27     7   11    11     2   14       M  

[5 rows x 35 columns]

## Concat

In [4]:
# here we are making it such that each game has two rows, where each one is a team view of the game with
# opposing metrics.

detailed_metrics = {
    "Score",
    "Loc", 
    "FGM",
    "FGA",
    "FGM3",
    "FTM",
    "FTA",
    "OR",
    "DR",
    "Ast",
    "Blk",
    "TO",
    "Stl",
    "PF",
}

w_renamed_cols = {f"W{col}": f"Team{col}" for col in detailed_metrics} | {f"L{col}": f"Opp{col}" for col in detailed_metrics}
l_renamed_cols = {f"L{col}": f"Team{col}" for col in detailed_metrics} | {f"W{col}": f"Opp{col}" for col in detailed_metrics}

In [5]:

detailed_reg_games_df = pd.concat([
    (
        detailed_reg_games_df[[col for col in detailed_reg_games_df.columns if col != "LTeamID"]]
        .assign(GameResult="W")
        .rename(columns=w_renamed_cols | {"WTeamID": "TeamID"})
    ),
    (
        detailed_reg_games_df[[col for col in detailed_reg_games_df.columns if col != "WTeamID"]]
        .assign(GameResult="L")
        .rename(columns=l_renamed_cols | {"LTeamID": "TeamID"})
    )

]).reset_index(drop=True)

detailed_reg_games_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 373324 entries, 0 to 373323
Data columns (total 36 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   Season      373324 non-null  int64 
 1   DayNum      373324 non-null  int64 
 2   TeamID      373324 non-null  int64 
 3   TeamScore   373324 non-null  int64 
 4   OppScore    373324 non-null  int64 
 5   TeamLoc     186662 non-null  object
 6   NumOT       373324 non-null  int64 
 7   TeamFGM     373324 non-null  int64 
 8   TeamFGA     373324 non-null  int64 
 9   TeamFGM3    373324 non-null  int64 
 10  WFGA3       373324 non-null  int64 
 11  TeamFTM     373324 non-null  int64 
 12  TeamFTA     373324 non-null  int64 
 13  TeamOR      373324 non-null  int64 
 14  TeamDR      373324 non-null  int64 
 15  TeamAst     373324 non-null  int64 
 16  TeamTO      373324 non-null  int64 
 17  TeamStl     373324 non-null  int64 
 18  TeamBlk     373324 non-null  int64 
 19  TeamPF      373324 non-

In [6]:
# do the same thing for the tournament games
detailed_tourney_games_df = pd.concat([
    (
        detailed_tourney_games_df[[col for col in detailed_tourney_games_df.columns if col != "LTeamID"]]
        .assign(GameResult="W")
        .rename(columns=w_renamed_cols | {"WTeamID": "TeamID"})
    ),
    (
        detailed_tourney_games_df[[col for col in detailed_tourney_games_df.columns if col != "WTeamID"]]
        .assign(GameResult="L")
        .rename(columns=l_renamed_cols | {"LTeamID": "TeamID"})
    )
]).reset_index(drop=True)

detailed_tourney_games_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4284 entries, 0 to 4283
Data columns (total 36 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Season      4284 non-null   int64 
 1   DayNum      4284 non-null   int64 
 2   TeamID      4284 non-null   int64 
 3   TeamScore   4284 non-null   int64 
 4   OppScore    4284 non-null   int64 
 5   TeamLoc     2142 non-null   object
 6   NumOT       4284 non-null   int64 
 7   TeamFGM     4284 non-null   int64 
 8   TeamFGA     4284 non-null   int64 
 9   TeamFGM3    4284 non-null   int64 
 10  WFGA3       4284 non-null   int64 
 11  TeamFTM     4284 non-null   int64 
 12  TeamFTA     4284 non-null   int64 
 13  TeamOR      4284 non-null   int64 
 14  TeamDR      4284 non-null   int64 
 15  TeamAst     4284 non-null   int64 
 16  TeamTO      4284 non-null   int64 
 17  TeamStl     4284 non-null   int64 
 18  TeamBlk     4284 non-null   int64 
 19  TeamPF      4284 non-null   int64 
 20  OppFGM  

In [7]:
detailed_reg_games_df["ScoreDiff"] = detailed_reg_games_df.apply(
    lambda row: row["TeamScore"] - row["OppScore"],
    axis=1,
)

detailed_tourney_games_df["ScoreDiff"] = detailed_tourney_games_df.apply(
    lambda row: row["TeamScore"] - row["OppScore"],
    axis=1,
)

In [8]:
detailed_reg_games_df["Win"] = detailed_reg_games_df.apply(
    lambda row: 0 if row["GameResult"] == "L" else 1,
    axis=1,
)

detailed_tourney_games_df["Win"] = detailed_tourney_games_df.apply(
    lambda row: 0 if row["GameResult"] == "L" else 1,
    axis=1,
)

## Aggregation

In [9]:
exclude_agg_cols = {
    "TeamID",
    "Season",
    "League",
    "GameResult",
    "OppLoc",
    "TeamLoc",
    "Season",
    "DayNum",
}

agg_funcs = [
    np.min,
    np.max,
    np.std,
    np.median,
    np.mean,
]

In [10]:
team_reg_agg = (
    detailed_reg_games_df.groupby(["TeamID", "Season", "League"])
    .agg({col: agg_funcs for col in detailed_reg_games_df.select_dtypes("number").columns if col not in exclude_agg_cols})
    .reset_index()
)

team_reg_agg.columns = [" ".join(col).strip() for col in team_reg_agg.columns.values]

team_reg_agg.sample(10, random_state=1)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
12348    3430    2012      W             41             78      10.808339   
6900     1431    2018      M             33             88      12.283247   
4406     1315    2014      M             43             95      10.019980   
4233     1307    2005      M             53            101      12.911860   
3407     1266    2008      M             51            100      11.841315   
5190     1352    2016      M             44             89      10.298567   
1892     1194    2005      M             45            104      14.194618   
10020    3270    2021      W             24             80      13.385137   
9567     3240    2014      W             43             84      11.319009   
12617    3452    2011      W             39             90      12.518374   

       TeamScore median  TeamScore mean  OppScore min  OppScore max  ...  \
12348              61.0       58.965517            36            85  ...   
6900               67.0       66.466667            44            97  ...   
4406               72.0       73.000000            61           103  ...   
4233               77.0       75.870968            47            81  ...   
3407               75.5       75.906250            37            89  ...   
5190               67.0       65.062500            45           106  ...   
1892               76.0       76.777778            59           107  ...   
10020              53.0       55.476190            41           117  ...   
9567               62.5       63.593750            45           100  ...   
12617              65.0       65.750000            21            79  ...   

       ScoreDiff min  ScoreDiff max  ScoreDiff std  ScoreDiff median  \
12348            -32             35      16.997102              -1.0   
6900             -49             29      14.772645              -5.0   
4406             -27             18      12.316786              -2.0   
4233             -17             34      13.022891              11.0   
3407             -20             47      17.828682              10.0   
5190             -62             18      14.365582              -7.0   
1892             -45             27      14.449736              -3.0   
10020            -93             24      27.245445             -15.0   
9567             -42             17      13.277095              -2.0   
12617            -23             57      18.777131              13.5   

       ScoreDiff mean  Win min  Win max   Win std  Win median  Win mean  
12348       -2.517241        0        1  0.508548         0.0  0.482759  
6900        -5.100000        0        1  0.479463         0.0  0.333333  
4406        -2.645161        0        1  0.508001         0.0  0.483871  
4233        10.935484        0        1  0.401610         1.0  0.806452  
3407        11.593750        0        1  0.456803         1.0  0.718750  
5190        -5.781250        0        1  0.470929         0.0  0.312500  
1892        -1.888889        0        1  0.492103         0.0  0.370370  
10020      -14.285714        0        1  0.462910         0.0  0.285714  
9567        -4.093750        0        1  0.504016         0.0  0.437500  
12617       13.500000        0        1  0.456803         1.0  0.718750  

[10 rows x 158 columns]

In [11]:
# aggregate the same metrics for the tournament dataset 

team_tourney_agg = (
    detailed_tourney_games_df.groupby(["TeamID", "Season", "League"])
    .agg({col: agg_funcs for col in detailed_tourney_games_df.select_dtypes("number").columns if col not in exclude_agg_cols})
    .reset_index()
)

team_tourney_agg.columns = [" ".join(col).strip() for col in team_tourney_agg.columns.values]

team_tourney_agg.sample(10, random_state=1)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
995     1390    2008      M             62             82      10.408330   
1601    3226    2021      W             63             63            NaN   
1805    3301    2023      W             63             63            NaN   
952     1373    2009      M             72             74       1.414214   
924     1361    2012      M             65             65            NaN   
1381    3124    2014      W             69             90       9.912114   
1266    1452    2021      M             72             84       8.485281   
1810    3304    2015      W             69             69            NaN   
697     1301    2023      M             63             63            NaN   
763     1323    2003      M             68             71       1.527525   

      TeamScore median  TeamScore mean  OppScore min  OppScore max  ...  \
995               77.0       73.666667            53            82  ...   
1601              63.0       63.000000            71            71  ...   
1805              63.0       63.000000            64            64  ...   
952               73.0       73.000000            72            79  ...   
924               65.0       65.000000            79            79  ...   
1381              81.0       80.250000            56            88  ...   
1266              78.0       78.000000            67            75  ...   
1810              69.0       69.000000            72            72  ...   
697               63.0       63.000000            72            72  ...   
763               70.0       69.666667            60            88  ...   

      ScoreDiff min  ScoreDiff max  ScoreDiff std  ScoreDiff median  \
995             -20             24      22.007574               1.0   
1601             -8             -8            NaN              -8.0   
1805             -1             -1            NaN              -1.0   
952              -7              2       6.363961              -2.5   
924             -14            -14            NaN             -14.0   
1381            -19             19      18.025445              15.5   
1266             -3             17      14.142136               7.0   
1810             -3             -3            NaN              -3.0   
697              -9             -9            NaN              -9.0   
763             -17              8      12.897028               1.0   

      ScoreDiff mean  Win min  Win max   Win std  Win median  Win mean  
995         1.666667        0        1  0.577350         1.0  0.666667  
1601       -8.000000        0        0       NaN         0.0  0.000000  
1805       -1.000000        0        0       NaN         0.0  0.000000  
952        -2.500000        0        1  0.707107         0.5  0.500000  
924       -14.000000        0        0       NaN         0.0  0.000000  
1381        7.750000        0        1  0.500000         1.0  0.750000  
1266        7.000000        0        1  0.707107         0.5  0.500000  
1810       -3.000000        0        0       NaN         0.0  0.000000  
697        -9.000000        0        0       NaN         0.0  0.000000  
763        -2.666667        0        1  0.577350         1.0  0.666667  

[10 rows x 158 columns]

## Join Aggregated w/ Attributes

In [12]:
conference_df = pd.concat([
    pd.read_csv(os.path.join(DATA_DIR, "MTeamConferences.csv")).assign(League="M"),
    pd.read_csv(os.path.join(DATA_DIR, "WTeamConferences.csv")).assign(League="W"),
])

team_conf_seeds_df = (
    conference_df.merge(
        right=(pd.concat([
            pd.read_csv(os.path.join(DATA_DIR, "MNCAATourneySeeds.csv")).assign(League="M"),
            pd.read_csv(os.path.join(DATA_DIR, "WNCAATourneySeeds.csv")).assign(League="W"),
        ])),
        on=["League", "Season", "TeamID"],
    )
    .merge(right=pd.read_csv(os.path.join(DATA_DIR, "MTeams.csv")), on="TeamID")
)

team_conf_seeds_df.sample(10, random_state=10)

Season  TeamID ConfAbbrev League Seed       TeamName  FirstD1Season  \
507     2016    1292       cusa      M  X15           MTSU           1985   
1174    1994    1438        acc      M  Z07       Virginia           1985   
1158    1998    1428        wac      M  X03           Utah           1985   
638     1988    1328  big_eight      M  Y01       Oklahoma           1985   
404     1999    1268        acc      M  Y02       Maryland           1985   
1797    2007    1308        wac      M  W13  New Mexico St           1985   
1471    1988    1185        mac      M  X15     E Michigan           1985   
1313    2021    1196        sec      M  Z07        Florida           1985   
881     1987    1424       pcaa      M  Z01           UNLV           1985   
1998    2006    1203      a_ten      M  W08   G Washington           1985   

      LastD1Season  
507           2024  
1174          2024  
1158          2024  
638           2024  
404           2024  
1797          2024  
1471          2024  
1313          2024  
881           2024  
1998          2024

In [13]:
# merge the team_conf_seeds_df with team attributes into the aggregated data

team_reg_agg_df = team_reg_agg.merge(right=team_conf_seeds_df, on=["TeamID", "Season", "League"])
team_tourney_agg_df = team_tourney_agg.merge(right=team_conf_seeds_df, on=["TeamID", "Season", "League"])

team_reg_agg_df.sample(10, random_state=10)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
976     1387    2012      M             58             86       7.354612   
834     1332    2019      M             47             84      11.186577   
305     1199    2011      M             44             97      13.496634   
124     1139    2016      M             55            144      16.508128   
1305    1458    2019      M             46            101      12.044032   
1174    1433    2019      M             49             90      10.441658   
567     1272    2004      M             60             94      10.228604   
665     1292    2013      M             45             97      11.877053   
271     1186    2004      M             49            100      12.568700   
325     1207    2011      M             46            111      14.956568   

      TeamScore median  TeamScore mean  OppScore min  OppScore max  ...  \
976               68.0       69.096774            35            79  ...   
834               72.0       70.485714            46            90  ...   
305               69.0       69.322581            38            89  ...   
124               78.0       80.580645            52            88  ...   
1305              69.0       69.060606            45            84  ...   
1174              70.5       71.437500            36            87  ...   
567               73.0       73.571429            48            85  ...   
665               72.0       71.242424            41            82  ...   
271               70.0       70.250000            52           104  ...   
325               69.0       71.032258            51           102  ...   

      Win min  Win max   Win std  Win median  Win mean  ConfAbbrev  Seed  \
976         0        1  0.425024         1.0  0.774194       a_ten   Z09   
834         0        1  0.481594         1.0  0.657143  pac_twelve   Z12   
305         0        1  0.475191         1.0  0.677419         acc   Z10   
124         0        1  0.475191         1.0  0.677419    big_east   X09   
1305        0        1  0.466694         1.0  0.696970     big_ten   Z05   
1174        0        1  0.420013         1.0  0.781250       a_ten   W08   
567         0        1  0.440959         1.0  0.750000        cusa   Y07   
665         0        1  0.364110         1.0  0.848485    sun_belt  Y11a   
271         0        1  0.503953         1.0  0.571429     big_sky   Y15   
325         0        1  0.475191         1.0  0.677419    big_east   Z06   

          TeamName  FirstD1Season  LastD1Season  
976       St Louis           1985          2024  
834         Oregon           1985          2024  
305     Florida St           1985          2024  
124         Butler           1985          2024  
1305     Wisconsin           1985          2024  
1174           VCU           1985          2024  
567        Memphis           1985          2024  
665           MTSU           1985          2024  
271   E Washington           1985          2024  
325     Georgetown           1985          2024  

[10 rows x 163 columns]

In [14]:
team_tourney_agg_df.sample(10, random_state=10)

TeamID  Season League  TeamScore min  TeamScore max  TeamScore std  \
1202    1437    2011      M             57             57            NaN   
109     1137    2013      M             56             56            NaN   
1105    1417    2015      M             60             92      17.925773   
700     1305    2005      M             59             61       1.414214   
834     1332    2019      M             49             73      13.576941   
1009    1393    2018      M             55             65       4.349329   
953     1373    2010      M             64             64            NaN   
1141    1425    2022      M             66             66            NaN   
419     1234    2015      M             68             83      10.606602   
973     1386    2008      M             64             64            NaN   

      TeamScore median  TeamScore mean  OppScore min  OppScore max  ...  \
1202              57.0       57.000000            61            61  ...   
109               56.0       56.000000            68            68  ...   
1105              62.0       71.333333            59            75  ...   
700               60.0       60.000000            57            71  ...   
834               72.0       64.666667            53            54  ...   
1009              58.5       59.250000            52            69  ...   
953               64.0       64.000000            72            72  ...   
1141              66.0       66.000000            68            68  ...   
419               75.5       75.500000            52            87  ...   
973               64.0       64.000000            72            72  ...   

      Win min  Win max   Win std  Win median  Win mean  ConfAbbrev  Seed  \
1202        0        0       NaN         0.0  0.000000    big_east   W09   
109         0        0       NaN         0.0  0.000000     patriot   W11   
1105        0        1  0.577350         1.0  0.666667  pac_twelve   X11   
700         0        1  0.707107         0.5  0.500000         wac   X09   
834         0        1  0.577350         1.0  0.666667  pac_twelve   Z12   
1009        0        1  0.500000         1.0  0.750000         acc  X11b   
953         0        0       NaN         0.0  0.000000        maac   X13   
1141        0        0       NaN         0.0  0.000000  pac_twelve   Y07   
419         0        1  0.707107         0.5  0.500000     big_ten   X07   
973         0        0       NaN         0.0  0.000000       a_ten   W11   

            TeamName  FirstD1Season  LastD1Season  
1202       Villanova           1985          2024  
109         Bucknell           1985          2024  
1105            UCLA           1985          2024  
700           Nevada           1985          2024  
834           Oregon           1985          2024  
1009        Syracuse           1985          2024  
953            Siena           1985          2024  
1141             USC           1985          2024  
419             Iowa           1985          2024  
973   St Joseph's PA           1985          2024  

[10 rows x 163 columns]

In [15]:
# merge the tournament aggregated metrics with the regular season aggregated metrics
team_agg_df = (
    pd.merge(
        left=team_reg_agg_df, 
        right=team_tourney_agg_df, 
        on=["TeamID", "Season", "League"], 
        suffixes=(" reg", " tourney"),
    )
)

In [16]:
team_agg_df.sample(10, random_state=1)

TeamID  Season League  TeamScore min reg  TeamScore max reg  \
409     1233    2013      M                 60                104   
1189    1436    2005      M                 55                 90   
1275    1455    2013      M                 52                 94   
487     1246    2017      M                 66                115   
1135    1425    2008      M                 46                 95   
556     1268    2007      M                 58                102   
368     1216    2021      M                 49                 83   
1037    1397    2023      M                 46                 94   
891     1345    2023      M                 54                 89   
559     1268    2015      M                 55                 95   

      TeamScore std reg  TeamScore median reg  TeamScore mean reg  \
409           11.901903                  81.0           80.696970   
1189           8.572611                  73.5           72.600000   
1275           9.407254                  69.0           69.441176   
487           12.687243                  87.0           85.941176   
1135          12.625978                  69.5           69.062500   
556           11.973088                  79.5           79.500000   
368           10.118859                  66.0           65.869565   
1037          11.188045                  71.0           71.787879   
891            9.013013                  74.5           73.088235   
559            9.364565                  68.0           69.484848   

      OppScore min reg  OppScore max reg  ...  Win min tourney  \
409                 57               105  ...                0   
1189                44                93  ...                0   
1275                39                91  ...                0   
487                 48               100  ...                0   
1135                44                96  ...                0   
556                 50               103  ...                0   
368                 50                87  ...                0   
1037                40                86  ...                0   
891                 39                79  ...                0   
559                 48                89  ...                0   

      Win max tourney  Win std tourney  Win median tourney  Win mean tourney  \
409                 0              NaN                 0.0          0.000000   
1189                1         0.707107                 0.5          0.500000   
1275                1         0.447214                 1.0          0.800000   
487                 1         0.500000                 1.0          0.750000   
1135                0              NaN                 0.0          0.000000   
556                 1         0.707107                 0.5          0.500000   
368                 0              NaN                 0.0          0.000000   
1037                1         0.577350                 1.0          0.666667   
891                 0              NaN                 0.0          0.000000   
559                 1         0.707107                 0.5          0.500000   

      ConfAbbrev tourney  Seed tourney  TeamName tourney  \
409                 maac           Z15              Iona   
1189                 aec           Y13           Vermont   
1275                 mvc           Z09        Wichita St   
487                  sec           Z02          Kentucky   
1135             pac_ten           X06               USC   
556                  acc           Y04          Maryland   
368                  aec           Z16          Hartford   
1037                 sec           W04         Tennessee   
891              big_ten           W01            Purdue   
559              big_ten           Y04          Maryland   

      FirstD1Season tourney  LastD1Season tourney  
409                    1985                  2024  
1189                   1985                  2024  
1275                   1985                  2024  
487      

In [17]:
# save it 
team_agg_df.to_csv(os.path.join(DATA_DIR, "AllTeamsAgg.csv"))